In [2]:
import pandas as pd
from scipy.stats import pearsonr
import plotly.graph_objects as go

In [48]:
df = pd.read_hdf("/home/wdecoster/wsl-repos/pathSTR-1000G/1000G.pathSTRdb", key="details")
df = df[["dataset", "gene", "length"]]
df["build"] = df["dataset"].apply(lambda x: x.split("_")[1])
df["caller"] = df["dataset"].apply(lambda x: x.split("_")[0])
df = df[df["caller"] == "STRdust"].drop(columns=["caller", "dataset"])
df.columns = ["_".join(col).strip() for col in df.columns.values]
df.reset_index(inplace=True)

df["identifier"] = df["sample"] + "_" + df["gene_"]
df = df.pivot(
    index="identifier", columns="build_", values=["length_Allele1", "length_Allele2"]
)


df.columns = ["_".join(col).strip().replace("length_", "") for col in df.columns.values]
df["hg38_long_allele"] = df[["Allele1_hg38", "Allele2_hg38"]].max(axis=1)
df["hg38_short_allele"] = df[["Allele1_hg38", "Allele2_hg38"]].min(axis=1)
df["t2t_long_allele"] = df[["Allele1_t2t", "Allele2_t2t"]].max(axis=1)
df["t2t_short_allele"] = df[["Allele1_t2t", "Allele2_t2t"]].min(axis=1)

df = df.dropna(subset=["t2t_long_allele"])

/tmp/ipykernel_805/3854164792.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



Empty DataFrame
Columns: [Allele1_hg38, Allele1_t2t, Allele2_hg38, Allele2_t2t, hg38_long_allele, hg38_short_allele, t2t_long_allele, t2t_short_allele]
Index: []

In [53]:
stat_long, p_long = pearsonr(df["hg38_long_allele"], df["t2t_long_allele"])
stat_short, p_short = pearsonr(df["hg38_short_allele"], df["t2t_short_allele"])
stat_both, p_both = pearsonr(df["hg38_long_allele"] + df["hg38_short_allele"], df["t2t_long_allele"] + df["t2t_short_allele"])

In [54]:
print(stat_long, p_long)
print(stat_short, p_short)
print(stat_both, p_both)

0.9826826283393628 0.0
0.7903824740980886 0.0
0.9546397282377707 0.0


In [55]:
def plot(df):
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=df["hg38_long_allele"], y=df["t2t_long_allele"], marker_color="blue", mode="markers", name="Long allele"))
    fig.add_trace(go.Scatter(x=df["hg38_short_allele"], y=df["t2t_short_allele"], marker_color="red", mode="markers", name="Short allele"))
    fig.update_traces(marker_size=2)
    fig.update_layout(
        title="hg38 vs. t2t",
        xaxis_title="hg38",
        yaxis_title="t2t",
        height=800,
        width=800,
        plot_bgcolor="rgba(0, 0, 0, 0)",
        paper_bgcolor="rgba(0, 0, 0, 0)",
        font=dict(size=16),
        legend=dict(yanchor="top", y=0.95, xanchor="left", x=0.01),
    )
    fig.update_xaxes(showline=True, linewidth=2, linecolor="black", mirror=True, showgrid=False, range=[0, 2000])
    fig.update_yaxes(showline=True, linewidth=2, linecolor="black", mirror=True, showgrid=False, range=[0, 2000])

    fig.add_annotation(
        x=0.5,
        y=0.9,
        xref="paper",
        yref="paper",
        text=f"<b>Pearson correlation coefficient</b><br>- long allele: {stat_long:.2f}<br>- short allele: {stat_short:.2f}<br>- combined: {stat_both:.2f}",
        showarrow=False,
        align="left",
    )
    return fig

In [56]:
plot(df).show()

In [57]:
# calculate the pearson correlation per repeat locus
df["locus"] = df.reset_index(drop=False)["identifier"].apply(lambda x: x.split("_")[1]).values

In [60]:
records = []
with open("correlation.html", "w") as f:
    for gene in df["locus"].unique():
        sub_df = df[df["locus"] == gene]
        stat_long, p_long = pearsonr(sub_df["hg38_long_allele"], sub_df["t2t_long_allele"])
        stat_short, p_short = pearsonr(sub_df["hg38_short_allele"], sub_df["t2t_short_allele"])
        stat_both, p_both = pearsonr(sub_df["hg38_long_allele"] + sub_df["hg38_short_allele"], sub_df["t2t_long_allele"] + sub_df["t2t_short_allele"])
        records.append((gene, stat_long, stat_short, stat_both))
        f.write(plot(sub_df).to_html())

In [61]:
stat = pd.DataFrame(records, columns=["locus", "stat_long", "stat_short", "stat_both"])

In [76]:
fig = stat.sort_values("stat_both").plot(y="locus", x="stat_both", kind='bar', backend="plotly")
fig.update_layout(
    title="Pearson correlation coefficient per repeat locus (hg38 vs. t2t)",
    xaxis_title="Pearson correlation coefficient",
    yaxis_title="Repeat locus",
    height=1200,
    width=800,
    plot_bgcolor="rgba(0, 0, 0, 0)",
    paper_bgcolor="rgba(0, 0, 0, 0)",
    font=dict(size=12),
)
# change the color of the bars to black
fig.update_traces(marker_color="black")
fig.update_xaxes(showline=True, linewidth=2, linecolor="black", mirror=True, showgrid=False, range=[0, 1])
fig.update_yaxes(showline=True, linewidth=2, linecolor="black", mirror=True, showgrid=False)
#rotate the x-axis labels 60 degrees
fig.update_xaxes(tickangle=60)